In [5]:
cd ..

/afs/inf.ed.ac.uk/user/s13/s1320903/Neuroglycerin/neukrill-net-work


In [2]:
import pylearn2.utils
import pylearn2.config
import theano
import neukrill_net.utils
import numpy as np
%matplotlib inline
import matplotlib.pyplot as plt
import holoviews as hl
%load_ext holoviews.ipython
import sklearn.metrics
import pickle
import neukrill_net.utils
import neukrill_net.encoding as enc
import neukrill_net.taxonomy as t

Using gpu device 1: Tesla K40c
:0: FutureWarning: IPython widgets are experimental and may change in the future.


Welcome to the HoloViews IPython extension! (http://ioam.github.io/holoviews/)
Available magics: %compositor, %opts, %params, %view, %%labels, %%opts, %%view


In [4]:
settings = neukrill_net.utils.Settings("settings.json")
run_settings = neukrill_net.utils.load_run_settings('run_settings/experiment_setting_colnorms_higher_aug.json', 
            settings, force=True)
model = pylearn2.utils.serial.load(run_settings['pickle abspath'])
# format the YAML
yaml_string = neukrill_net.utils.format_yaml(run_settings, settings)
# load proxied objects
proxied = pylearn2.config.yaml_parse.load(yaml_string, instantiate=False)
# pull out proxied dataset
proxdata = proxied.keywords['dataset']
# force loading of dataset and switch to test dataset
proxdata.keywords['force'] = True
proxdata.keywords['training_set_mode'] = 'test'
proxdata.keywords['verbose'] = False
# then instantiate the dataset
dataset = pylearn2.config.yaml_parse._instantiate(proxdata)
if hasattr(dataset.X, 'shape'):
    N_examples = dataset.X.shape[0]
else:
    N_examples = len(dataset.X)
batch_size = 500
while N_examples%batch_size != 0:
    batch_size += 1
n_batches = int(N_examples/batch_size)
#n_classes = len(settings.classes)
model.set_batch_size(batch_size)
X = model.get_input_space().make_batch_theano()
Y = model.fprop(X)
if type(X) == tuple:
    f = theano.function(X,Y)
else:
    f = theano.function([X],Y)
augment = 1
y = np.zeros((N_examples*augment,188))
# get the data specs from the cost function using the model
pcost = proxied.keywords['algorithm'].keywords['cost']
cost = pylearn2.config.yaml_parse._instantiate(pcost)
data_specs = cost.get_data_specs(model)
i = 0
for _ in range(augment):
    # make sequential iterator
    iterator = dataset.iterator(batch_size=batch_size,num_batches=n_batches,
                        mode='even_sequential', data_specs=data_specs)
    for batch in iterator:
        if type(X) == tuple:
            y[i*batch_size:(i+1)*batch_size,:] = f(batch[0],batch[1])
        else:
            y[i*batch_size:(i+1)*batch_size,:] = f(batch[0])
        i += 1
af = run_settings.get("augmentation_factor",1)
if af > 1:
    y_collapsed = np.zeros((int(N_examples/af), 188)) 
    for i,(low,high) in enumerate(zip(range(0,dataset.y.shape[0],af),
                                range(af,dataset.y.shape[0]+af,af))):
        y_collapsed[i,:] = np.mean(y[low:high,:], axis=0)
    y = y_collapsed
    # and collapse labels
    labels = dataset.y[range(0,dataset.y.shape[0],af)]
elif augment > 1:
    y_collapsed = np.zeros((N_examples,188))
    # different kind of augmentation, has to be collapsed differently
    for row in range(N_examples):
        y_collapsed[row,:] = np.mean(np.vstack([r for r in 
            y[[i for i in range(row,N_examples*augment,N_examples)],:]]), 
            axis=0)
    y = y_collapsed            
    labels = dataset.y
else:
    labels = dataset.y

In [5]:
y.shape

(3089, 188)

In [6]:
predictions = np.zeros(y.shape)
np.copyto(predictions, y)
predictions.shape

(3089, 188)

In [7]:
import neukrill_net.taxonomy as t
only_leaf_children = []
hier = enc.get_hierarchy(settings)

layer = t.TaxonomyLayer(1)

for s in hier[1]:
    flag = True
    for key, values in t.superclasses.items():
        for i, v in enumerate(values):
            if v == s and i != 1:
                flag = False
    if flag:
        if s not in only_leaf_children:
            only_leaf_children.append(s)

In [8]:
only_leaf_children

['acantharia',
 'appendicularians',
 'calanoid',
 'chaetognaths',
 'cydippid',
 'decapods_all',
 'detritus',
 'diatoms',
 'euphausiids_all_ages',
 'fish',
 'no_class',
 'oithona',
 'other_hydromedusae',
 'physonect',
 'pluteus',
 'pteropods',
 'radiolarian',
 'rocketship',
 'seastar',
 'sphaeronectes',
 'sub_hydromedusae1',
 'sub_hydromedusae2',
 'sub_protists',
 'trichodesmium',
 'tunicate',
 'unknown']

In [9]:
superclasses2 = np.zeros((y.shape[0], 16))
np.copyto(superclasses2, predictions[:,(121+38):(121+38+16)])
superclasses2.shape

(3089, 16)

In [10]:
superclass2_children = {}
settings = neukrill_net.utils.Settings("settings.json")
hier = enc.get_hierarchy(settings)

for s in hier[2]:
    children = []
    for key, values in t.superclasses.items():
        for i, v in enumerate(values):
            if s == v:
                if i > 0:
                    if values[i-1] not in children:
                        children.append(values[i-1])
    superclass2_children[s] = children

In [11]:
superclass2_children

{'calycophoran_siphonophores': ['rocketship',
  'sphaeronectes',
  'siphonophore_calycophoran_abylidae'],
 'copepods': ['calanoid', 'cyclopoid_copepods'],
 'crustaceans': ['shrimp_like',
  'copepods',
  'stomatopod',
  'amphipods',
  'crustacean_other'],
 'ctenophores': ['ctenophore_cestid', 'ctenophore_lobate', 'cydippid'],
 'cyclopoid_copepods': ['oithona', 'copepod_cyclopoid_copilia'],
 'echinoderm': ['seastar',
  'echinoderm_seacucumber_auricularia_larva',
  'pluteus'],
 'gastropods': ['pteropods', 'heteropod'],
 'gelatinous zooplankton': ['ctenophores',
  'pelagic_tunicates',
  'hydromedusae',
  'siphonophores',
  'ephyra',
  'jellies_tentacles'],
 'hydromedusae': ['other_hydromedusae',
  'sub_hydromedusae2',
  'sub_hydromedusae1'],
 'no_class': ['artifacts', 'artifacts_edge'],
 'other_invert_larvae': ['echinoderm',
  'tornaria_acorn_worm_larvae',
  'trochophore_larvae',
  'invertebrate_larvae_other_A',
  'invertebrate_larvae_other_B'],
 'pelagic_tunicates': ['appendicularians', '

In [12]:
nr = np.zeros((y.shape[0], 121))
np.copyto(nr, predictions[:,:121])
weight = 0.01
nr.shape

(3089, 121)

In [ ]:
layer = t.TaxonomyLayer(1)
weight = 0.01

for index, row in enumerate(nr):
    for key, value in superclass2_children.items():
        proportion = 0
        leaf = []
        for i,v in enumerate(value):
            if v in only_leaf_children:
                update = {}
                for i, c in enumerate(settings.classes):
                    if v == layer[c]:
                        update[i] = settings.class_priors[i]
                denom = sum(v for k,v in update.items())
                proportion += denom
                indUpdate = [k for k,v in update.items()]
                row[indUpdate] = row[indUpdate] * (1-weight) + [v for k,v in update.items()/denom * weight]
            else:
                if v in settings.classes:
                    leaf.append(i) 
        for l in leaf:
            col = int(np.where(np.array(hier[2]) == key)[0])
            row[i] = (superclasses2[row, col] - proportion)
    if index%1000 == 0:
    print index
        

[  9.98529964e-01   7.37711786e-04   7.30124076e-04   2.74924681e-15
   1.12596497e-18   9.97450249e-20   2.95078822e-19   7.96512643e-18
   4.07667508e-16   1.20062632e-15   2.16886575e-17   2.44781595e-15
   1.95282553e-17   2.36403566e-18   1.77103644e-11   8.27115365e-17
   1.51734975e-14   2.51452043e-15   7.82034011e-14   3.08219514e-15
   2.42589264e-18   6.11954335e-13   2.34407491e-13   7.93886130e-17
   2.06207656e-16   3.72602890e-15   2.87335599e-14   4.03988807e-18
   7.24374826e-21   6.74299396e-18   2.11360335e-13   9.06943406e-18
   5.24421716e-20   6.19541094e-13   7.04685659e-13   4.46554217e-11
   2.50852828e-11   1.13929641e-14   5.84330895e-09   2.54163895e-11
   1.86249270e-06   1.62784772e-10   1.75504075e-14   4.32162647e-15
   6.12821410e-19   2.83428120e-13   4.67824535e-17   3.87268030e-17
   5.28097952e-18   1.41001314e-14   8.51003745e-18   8.38094278e-19
   1.24320531e-18   3.23111823e-18   1.05100928e-18   1.03741768e-19
   2.77439190e-17   5.47781005e-12